### Downloading and Visualizing OSM Data with LeafMap

[Leafmap](https://leafmap.org/) comes with handy utilities to work with OpenStreetMap data. Using the popular package OSMNx in the background, it provides utility functions to download and visualize data from the OSM database.

* [Leafmap OpenStreetMap Features](https://leafmap.org/notebooks/15_openstreetmap/)
* [`leafmap.osm` module](https://leafmap.org/osm/)

#### Setup and Data Download

In [ ]:
%%capture
if 'google.colab' in str(get_ipython()):
  !apt install libspatialindex-dev
  !pip install fiona shapely pyproj rtree mapclassify
  !pip install geopandas
  !pip install leafmap
  !pip install osmnx

In [1]:
import os
import geopandas as gpd
import folium
import leafmap.foliumap as leafmap
import osmnx

In [2]:
data_folder = 'data'
output_folder = 'output'

if not os.path.exists(data_folder):
    os.mkdir(data_folder)
if not os.path.exists(output_folder):
    os.mkdir(output_folder)

#### Downloading OSM Data

We can easily download data for a city or a region by its name using the `leafmap.osm_gdf_from_place()` function. We can specify the list of required tags using a dictionary. See [OSM Wiki](https://wiki.openstreetmap.org/wiki/Map_features) for a complete list of tags and values.

You can also download data using a bounding box using `leafmap.osm.osm_gdf_from_bbox()` function.

Reference: [`leafmap.osm_gdf_from_place`](https://leafmap.org/osm/#leafmap.osm.osm_gdf_from_place)

In [11]:
parking_gdf = leafmap.osm_gdf_from_place(
    'Krakow',
    tags={'amenity': ['parking', 'parking_space', 'parking_entrance']}
  )

/home/stephen137/mambaforge/lib/python3.10/site-packages/leafmap/osm.py:78: UserWarning: The `utils.config` function is deprecated and will be removed in a future release. Instead, use the `settings` module directly to configure a global setting's value. For example, `ox.settings.log_console=True`.
  ox.config(use_cache=True, log_console=False)
/home/stephen137/mambaforge/lib/python3.10/site-packages/leafmap/osm.py:80: UserWarning: The `geometries` module and `geometries_from_X` functions have been renamed the `features` module and `features_from_X` functions. Use these instead. The `geometries` module and function names are deprecated and will be removed in a future release.
  gdf = ox.geometries_from_place(query, tags, which_result, buffer_dist)


In [12]:
parking_gdf

access           amenity  parking  \
element_type osmid                                             
node         236101747    private           parking  surface   
             274507373        NaN           parking      NaN   
             287598349    private           parking  surface   
             287598381        NaN           parking      NaN   
             321430146  customers  parking_entrance      NaN   
...                           ...               ...      ...   
relation     15415999   customers           parking  surface   
             15487336     private           parking  surface   
             15526265         NaN           parking  surface   
             15913033     private           parking  surface   
             16009805         NaN           parking      NaN   

                                                                 geometry  \
element_type osmid                                                          
node         236101747                          POINT (19.89324 50.08971)   
             274507373                          POINT (19.91338 50.09250)   
             287598349                          POINT (20.01206 50.01466)   
             287598381                          POINT (20.01040 50.01109)   
             321430146                          POINT (19.92312 50.03296)   
...                                                                   ...   
relation     15415999   POLYGON ((20.15197 50.06823, 20.15196 50.06827...   
             15487336   POLYGON ((19.92270 50.09384, 19.92268 50.09385...   
             15526265   POLYGON ((19.95290 50.08756, 19.95338 50.08802...   
             15913033   POLYGON ((20.01881 50.01493, 20.01856 50.01492...   
             16009805   POLYGON ((19.98665 50.00503, 19.98668 50.00502...   

                            created_by barrier covered  fee  lit supervised  \
element_type osmid                                                            
node         236101747             NaN     NaN     NaN  NaN  NaN        NaN   
             274507373             NaN     NaN     NaN  NaN  NaN        NaN   
             287598349  Potlatch 0.10b     NaN     NaN  NaN  NaN        NaN   
             287598381  Potlatch 0.10b     NaN     NaN  NaN  NaN        NaN   
             321430146             NaN     NaN     yes   no  yes         no   
...                                ...     ...     ...  ...  ...        ...   
relation     15415999              NaN     NaN     NaN  NaN  NaN        NaN   
             15487336              NaN     NaN     NaN  NaN  NaN        NaN   
             15526265              NaN     NaN     NaN  NaN  NaN        NaN   
             15913033              NaN     NaN     NaN   no  NaN        NaN   
             16009805              NaN     NaN     NaN  NaN  NaN        NaN   

                        ... construction comment access:parent seasonal  hgv  \
element_type osmid      ...                                                    
node         236101747  ...          NaN     NaN           NaN      NaN  NaN   
             274507373  ...          NaN     NaN           NaN      NaN  NaN   
             287598349  ...          NaN     NaN           NaN      NaN  NaN   
             287598381  ...          NaN     NaN           NaN      NaN  NaN   
             321430146  ...          NaN     NaN           NaN      NaN  NaN   
...                     ...          ...     ...           ...      ...  ...   
relation     15415999   ...          NaN     NaN           NaN      NaN  NaN   
             15487336   ...          NaN     NaN           NaN      NaN  NaN   
             15526265   ...          NaN     NaN           NaN      NaN  NaN   
             15913033   ...          NaN     NaN           NaN      NaN  NaN   
             16009805   ...          NaN     NaN           NaN      NaN  NaN   

                       parking:orientation check_date  \
element_type osmid                                      
node     

The GeoDataFrame has a hierarchical MultiIndex. Let's flatten it using `reset_index()`

In [13]:
parking_gdf = parking_gdf.reset_index(level=[0,1])

The result has many columns. Let's filter to required columns.

In [14]:
parking_gdf_subset = parking_gdf[['amenity','parking', 'access', 'geometry']]

The results contains both points(locations) and polygon(zones) features. Let's separate them out.

In [15]:
parking_zones = parking_gdf_subset[
    parking_gdf_subset['geometry'].apply(lambda x : x.type == 'Polygon' )]

parking_locations = parking_gdf_subset[
    parking_gdf_subset['geometry'].apply(lambda x : x.type == 'Point' )]

/tmp/ipykernel_815/2266268312.py:2: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  parking_gdf_subset['geometry'].apply(lambda x : x.type == 'Polygon' )]
/tmp/ipykernel_815/2266268312.py:5: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  parking_gdf_subset['geometry'].apply(lambda x : x.type == 'Point' )]


We can save the resulting GeoDataFrame to a GeoPackage.

In [16]:
# save GeoDataFrame to .gpkg
output_file = 'parking.gpkg'
output_path = os.path.join(output_folder, output_file)
parking_zones.to_file(driver='GPKG', filename=output_path, layer='zones') # create layer names for acessing from .gpkg
parking_locations.to_file(driver='GPKG', filename=output_path, layer='locations') # create layer names for acesssing from .gpkg

### Visualizing OSM Data

The `leafmap.osm` module has many functions that can add OSM data directy to the map. Here we use `add_osm_from_geocode()` function to add the boundary of a region from OSM. In addition, we can select a basemap from `leafmap.basemaps.keys()` for the map.

In [17]:
m = leafmap.Map(width=800, height=500)
m.add_basemap('CartoDB.DarkMatter')
m.add_osm_from_geocode('Krakow', layer_name='Krakow', info_mode=None)
m

We can add the GeoDataFrame to the map as well using GeoPanda's `explore()` function which allows us to customize the marker's shape, size for the point layer.

In [19]:
m = leafmap.Map(width=800, height=500)

m.add_basemap('CartoDB.DarkMatter')
m.add_osm_from_geocode('Krakow', layer_name='Krakow', info_mode=None)

parking_zones.explore(
    style_kwds={'fillOpacity': 0.3, 'weight': 0.5},
    color='purple',
    name='parking zones',
    m=m)

parking_locations.explore(
    marker_type='circle',
    marker_kwds={'radius': 1},
    color='yellow',
    name='parking locations',
    m=m)
m